In [1]:
import pandas as pd

import MyLib.nlp as nlp
import MyLib.HTML_prep as HTML_prep
import MyLib.analysis as analysis 
%load_ext autoreload
%autoreload 2

## My API key  & library_Id are stored in another file
api_key,library_id = pd.read_json("Zotero_API_key.json", typ='series')

library_type="group"

def print_time():
    from datetime import datetime
    now = datetime.now()
    current_time = now.strftime("%H:%M:%S")
    print("Current Time =", current_time)


from pyzotero import zotero
zot = zotero.Zotero(library_id, library_type, api_key)

ID_Universities='EWSYI3RS' # to access the files in the university subfolder.
ID_SURF='WPXRQVIU'

In [2]:
helpDict={}

for i in zot.collections_sub(ID_Universities):
    name,key=i["data"]["name"],i["data"]["key"]
    print(f"name: {name} --> key: {key}")
    collection_items=zot.collection_items(key)
    helpDict.update({k["key"]:k["data"]|{"Uni":name} for k in collection_items})
    
#Add Surf
name="surf"
key=ID_SURF
print(f"name: {name} --> key: {key}")
collection_items=zot.collection_items(key)
helpDict.update({k["key"]:k["data"]|{"Uni":name} for k in collection_items})

name: Radboud Nijmegen --> key: 5JQEUPHJ
name: Leiden University --> key: P483KEM8
name: OpenUniversiteitNederland --> key: X4HX8ZQE
name: Wageningen University --> key: QMTMEV7G
name: University of Twente --> key: QFGTICY2
name: Utrecht University --> key: 9A2UJIVA
name: Rotterdam University --> key: Z4EJ3VVG
name: University of Groningen --> key: P63XN58M
name: Vrije Universiteit Amsterdam --> key: AZJ9ZEBZ
name: Tilburg University --> key: XF9572P7
name: Eindhoven University of Technoloy --> key: FKNPJ5UD
name: Maastricht Univerisity --> key: QW34VSNN
name: Delft University --> key: FZDYP465
name: University of Amsterdam --> key: 92FECCMX
name: surf --> key: WPXRQVIU


In [3]:
df=pd.DataFrame(helpDict).T

In [4]:
Claimed_Parents=df["parentItem"].dropna().to_list()
Real_Parents=df.index.to_list()
WithoutParents=list(set(Claimed_Parents)-set(Real_Parents))
WithoutParents

['YFVXGF9R',
 'LC8BSUCF',
 'R25BZBVD',
 '6QUWHMGJ',
 'V99PPBFA',
 'Y4ZK2W9D',
 'PFAENAWF',
 '8HW32ESW',
 'X9Q76XGF',
 '2ML9YRW5',
 'ZUAIJQSB']

In [5]:
Parents_columns=['title', 'date','itemType','language']
WithParents_columns=["key",'parentItem','url','filename',"Uni"]

WithParents=df.dropna(subset="parentItem")[WithParents_columns]
Parents=df[df.itemType.apply(lambda x: x!="attachment")][Parents_columns]

df=WithParents.merge(Parents, left_on="parentItem",right_index=True, how="right")
df.head(5)

#df2[df2.filename.isna()].itemType

key parentItem  \
KYXS34U3  KYXS34U3   8GFU28PG   
SCJTRZZG  SCJTRZZG   PVW7P2K2   
T7YB6RJC  T7YB6RJC   LZZSGAT9   
RAM5QEQA  RAM5QEQA   DAWT2QFC   
MABYLJWJ  MABYLJWJ   AYXM9BDE   

                                                        url  \
KYXS34U3                      https://www.ru.nl/en/cls/clst   
SCJTRZZG                     https://clinical-nlp.cs.ru.nl/   
T7YB6RJC  https://www.ru.nl/over-ons/nieuws/nolai-verken...   
RAM5QEQA  https://neerlandistiek.nl/2023/01/taalkundig-r...   
MABYLJWJ  https://theses.ubn.ru.nl/bitstreams/e9ce4c6e-c...   

                                                   filename               Uni  \
KYXS34U3                                          clst.html  Radboud Nijmegen   
SCJTRZZG                         clinical-nlp.cs.ru.nl.html  Radboud Nijmegen   
T7YB6RJC  nolai-verkent-de-drieminutentoets-zo-gaat-dat-...  Radboud Nijmegen   
RAM5QEQA              taalkundig-redeneren-met-chatgpt.html  Radboud Nijmegen   
MABYLJWJ                     Leeuw_2022_Can AI help you.pdf  Radboud Nijmegen   

                                                      title  \
KYXS34U3  Centre for Language and Speech Technology | Ra...   
SCJTRZZG                  2nd Dutch Meeting on Clinical NLP   
T7YB6RJC  NOLAI verkent de drieminutentoets, zo gaat dat...   
RAM5QEQA                   Taalkundig redeneren met ChatGPT   
MABYLJWJ         Can AI help you? – A banking chatbot study   

                               date        itemType language  
KYXS34U3                 2023-06-28         webpage       en  
SCJTRZZG                                    webpage       en  
T7YB6RJC                 2023-03-06         webpage       nl  
RAM5QEQA  2023-01-14T10:00:00+00:00         webpage    nl-NL  
MABYLJWJ                 2022-07-19  journalArticle       en

In [6]:
df.Uni.value_counts()

Uni
University of Twente                 56
Delft University                     52
Leiden University                    50
Eindhoven University of Technoloy    50
University of Amsterdam              49
surf                                 49
Radboud Nijmegen                     47
Utrecht University                   45
Vrije Universiteit Amsterdam         45
Maastricht Univerisity               42
Tilburg University                   40
Rotterdam University                 33
University of Groningen              20
OpenUniversiteitNederland            16
Wageningen University                16
Name: count, dtype: int64

In [7]:
# Correct item type of uTwente Thesies
df.loc[df.url.apply(lambda x: "essay.utwente.nl" in str(x)),"itemType"]="thesis"
print(df.itemType.value_counts())

itemType
webpage             375
journalArticle      147
thesis               38
document             31
blogPost             24
conferencePaper      19
note                 16
book                  6
bookSection           3
dataset               2
film                  1
newspaperArticle      1
Name: count, dtype: int64


In [8]:
# remove not useful items
DropTypeList=["journalArticle","conferencePaper","thesis","book","bookSection","note","film","dataset"]

df=df[~df["itemType"].isin(DropTypeList)]

print(df.itemType.value_counts())

itemType
webpage             375
document             31
blogPost             24
newspaperArticle      1
Name: count, dtype: int64


In [9]:
def fileName(key,filename):
    DIR=f"C:\\Users\\mr\\Zotero\\storage\\{key}\\"
    filename=DIR+str(filename)
    return filename

df["filepath"]=df.apply(lambda x: fileName(x.key, x.filename), axis=1).drop_duplicates()

print(df.filepath[0],print(len(df)))

431
C:\Users\mr\Zotero\storage\KYXS34U3\clst.html None


In [10]:
df.to_json("2023-07-30_Uni_Files_raw.json")
# CHeck for duplicates / errors in Zotero: 
df[df.index.duplicated()]

Empty DataFrame
Columns: [key, parentItem, url, filename, Uni, title, date, itemType, language, filepath]
Index: []

In [ ]:
df=pd.read_json("2023-07-27_Uni_Files_raw.json")

# Add Content from PDFs

In [11]:
def getLinksfromPDF(page):
    links=[]

    if '/Annots' in page.keys():
        annotations=page['/Annots']
        for a in annotations:
            a=a.get_object()
            if '/A' in a:
                A=a['/A']
                if '/URI' in A.keys():
                    link=(A['/URI'])
                    links.append(link)
    return links

def getDate(pdf_reader):
    mod_date=None
    metaData=pdf_reader.metadata
    if '/ModDate' in metaData.keys():
        #print(metaData.keys())
        mod_date=metaData['/ModDate'][2:10]
        dtformat = "%Y%m%d"
        mod_date=pd.to_datetime(mod_date,format=dtformat)
        #print(creation_date)
    return mod_date
    
def extract_text_with_pyPDF(filepath,MaxPages=20):
    
    pages,links,mod_date=[],[],None
    from pypdf import PdfReader
    
    pdf_reader = PdfReader(filepath)
    mod_date=getDate(pdf_reader)
    
    S_pages=pdf_reader.pages
    if len(S_pages)>MaxPages:
        f=filepath.split("\\")[-1]
        #print(f"{f} has more than {MaxPages} pages: {len(S_pages)}. Only processing {MaxPages} pages.")
        S_pages=S_pages[:MaxPages]

    for i, page in enumerate(S_pages):
        raw_text = ""
        try:
            text = page.extract_text()
            if text:
                raw_text += text
                pages.append(raw_text)
        except Exception as error:
            print("text-problems with: ", filepath)
            print("\n", error)
            
    for i, page in enumerate(S_pages):
        links=getLinksfromPDF(page)

    return pd.Series([pages,links,mod_date])

    
PDFs=df.loc[df.filepath.apply(lambda x: x.split(".")[-1]=="pdf"),["filepath","date"]]    
NumberOfPDFs=len(PDFs)    

print(f"the dataset containts {NumberOfPDFs} PDF-files.")

df[["text","links","mod_date"]]=PDFs.filepath.apply(extract_text_with_pyPDF,MaxPages=150)

# Use filemod as date.
df.loc[~df.mod_date.isna(),["date"]]=df.mod_date
df.drop(columns='mod_date',inplace=True)

#problemfile.filepath.apply(extract_text_with_pyPDF,MaxPages=10)

the dataset containts 31 PDF-files.


# Add Content from HTMLs

In [12]:
def find_date(url, date):
    from htmldate import find_date
    from numpy import nan
    if type(date)!=pd.Timestamp:
        try:
            date=pd.to_datetime(find_date(url))
        except:
            date=nan
    return date


print("This takes about: 3 minutes.")

df["date"]=df.date.apply(pd.to_datetime,errors='coerce')
print_time()     

df["date"]=df.apply(lambda x: find_date(x.url, x.date), axis=1)
print_time()

df.date.apply(lambda x: type(x)==pd.Timestamp).value_counts()

This takes about: 3 minutes.
Current Time = 10:54:06


C:\Users\mr\miniconda3\envs\PyMax\lib\site-packages\dateutil\parser\_parser.py:1207: UnknownTimezoneWarning: tzname CEST identified but not understood.  Pass `tzinfos` argument in order to correctly return a timezone-aware datetime.  In a future version, this will raise an exception.
  warnings.warn("tzname {tzname} identified but not understood.  "
C:\Users\mr\miniconda3\envs\PyMax\lib\site-packages\dateutil\parser\_parser.py:1207: UnknownTimezoneWarning: tzname CET identified but not understood.  Pass `tzinfos` argument in order to correctly return a timezone-aware datetime.  In a future version, this will raise an exception.
  warnings.warn("tzname {tzname} identified but not understood.  "
C:\Users\mr\AppData\Local\Temp\ipykernel_21860\1949814470.py:14: UserWarning: Parsing dates in %d.%m.%Y format when dayfirst=False (the default) was specified. Pass `dayfirst=True` or specify a format to silence this warning.
  df["date"]=df.date.apply(pd.to_datetime,errors='coerce')


Current Time = 10:57:10


date
True     407
False     24
Name: count, dtype: int64

In [13]:
df.to_json("2023-07-30_Uni_Files_raw_date.json")

In [ ]:
df=pd.read_json("2023-07-30_Uni_Files_raw_date.json")

In [24]:
df

key  \
KYXS34U3  KYXS34U3   
SCJTRZZG  SCJTRZZG   
T7YB6RJC  T7YB6RJC   
RAM5QEQA  RAM5QEQA   
QJ4WZUBB  QJ4WZUBB   
...            ...   
9AIE24VD  9AIE24VD   
KU5NULID  KU5NULID   
9QNG3ET3  9QNG3ET3   
J7EHNKS5  J7EHNKS5   
VTWCZBP7  VTWCZBP7   

                                                                                                                                    url  \
KYXS34U3                                                                                                  https://www.ru.nl/en/cls/clst   
SCJTRZZG                                                                                                 https://clinical-nlp.cs.ru.nl/   
T7YB6RJC                                            https://www.ru.nl/over-ons/nieuws/nolai-verkent-de-drieminutentoets-zo-gaat-dat-dus   
RAM5QEQA                                                            https://neerlandistiek.nl/2023/01/taalkundig-redeneren-met-chatgpt/   
QJ4WZUBB                                                             https://www.ru.nl/communicationscience/research/research-projects/   
...                                                                                                                                 ...   
9AIE24VD   https://communities.surf.nl/ai-in-education/artikel/de-europese-commissie-vraagt-om-input-op-ethische-richtlijnen-voor-ai-en   
KU5NULID  https://communities.surf.nl/vraagbaak-online-onderwijs/artikel/tips-discussies-en-verhalen-over-digitale-onderwijsinnovatie-5   
9QNG3ET3  https://communities.surf.nl/vraagbaak-online-onderwijs/artikel/tips-discussies-en-verhalen-over-digitale-onderwijsinnovatie-4   
J7EHNKS5                         https://communities.surf.nl/vraagbaak-online-onderwijs/artikel/deze-artikelen-werden-het-meest-gelezen   
VTWCZBP7   https://communities.surf.nl/vraagbaak-online-onderwijs/artikel/deze-linkedin-posts-over-digitale-onderwijsinnovatie-wil-je-1   

                                                                               filename  \
KYXS34U3                                                                      clst.html   
SCJTRZZG                                                     clinical-nlp.cs.ru.nl.html   
T7YB6RJC                         nolai-verkent-de-drieminutentoets-zo-gaat-dat-dus.html   
RAM5QEQA                                          taalkundig-redeneren-met-chatgpt.html   
QJ4WZUBB                                                         research-projects.html   
...                                                                                 ...   
9AIE24VD  de-europese-commissie-vraagt-om-input-op-ethische-richtlijnen-voor-ai-en.html   
KU5NULID            tips-discussies-en-verhalen-over-digitale-onderwijsinnovatie-5.html   
9QNG3ET3            tips-discussies-en-verhalen-over-digitale-onderwijsinnovatie-4.html   
J7EHNKS5                                   deze-artikelen-werden-het-meest-gelezen.html   
VTWCZBP7             deze-linkedin-posts-over-digitale-onderwijsinnovatie-wil-je-1.html   

                       Uni  \
KYXS34U3  Radboud Nijmegen   
SCJTRZZG  Radboud Nijmegen   
T7YB6RJC  Radboud Nijmegen   
RAM5QEQA  Radboud Nijmegen   
QJ4WZUBB  Radboud Nijmegen   
...                    ...   
9AIE24VD              surf   
KU5NULID              surf   
9QNG3ET3              surf   
J7EHNKS5              surf   
VTWCZBP7              surf   

                                                                                                                      title  \
KYXS34U3                                                     Centre for Language and Speech Technology | Radboud University   
SCJTRZZG                                                                                  2nd Dutch meeting on Clinical NLP   
T7YB6RJC                                          NOLAI verkent de drieminutentoets, zo gaat dat dus | Radboud Universiteit   
RAM5QEQA                                                                                   Taalkundig redeneren met Cha

In [14]:
def FileInfo(FilePath):
    Title,h1,h2,h3,text,linkName,linkUrl=None,None,None,None,None,None,None

    if FilePath.endswith(".html"):
           
        try:
            #print(FilePath)

            with open(FilePath,"r", encoding='utf-8') as f:
                text= f.read()
            
        except:
            print("error opening the html file. File does not exist?")
            return
        
        
        try:
            from bs4 import BeautifulSoup

            soup = BeautifulSoup(text, "html5lib") #'html.parser')       
            Title=soup.title.text
            #soup=HTML_prep.removeIMGs(soup,IMG_filename=Title.replace(" ","_"))
            
            TextIndicators=soup("p")+soup("h5")+soup("h4")+soup("h3")+soup("h2")+soup("h1")

            All_divs=[p.parent for p in TextIndicators if p.parent.name in ["div","main","section","article","center","td"]]
     
            All_divs=list(dict.fromkeys(All_divs))
            
            
            # Remove images
            try:
                IMG_filename="".join(x for x in Title.strip().replace(" ","_") if x.isalnum() or x=="_")[:100]
                All_divs=[HTML_prep.removeIMGs(div,write_img=False,IMG_filename=IMG_filename) for div in All_divs]        
            except:
                print(f"error removing images: {FilePath}")
                
            h1=[item for sublist in [[i.text for i in div("h1")] for div in All_divs if div("h1")!=None] for item in sublist]
            h2=[item for sublist in [[i.text for i in div("h2")] for div in All_divs if div("h2")!=None] for item in sublist]
            h3=[item for sublist in [[i.text for i in div("h3")] for div in All_divs if div("h3")!=None] for item in sublist]
        

            # here only get all divs
            #text=[item for sublist in [[i.text for i in div("p")] for div in All_divs if div("p")!=None] for item in sublist]
            
            # here gets all human readable text parts --> includes headlines. the \n \n keeps distance to headlines
           
            linkName=[item for sublist in [[i.text for i in div("a")] for div in All_divs if div("a")!=None] for item in sublist]
            linkUrl=[item for sublist in [[i.get('href') for i in div("a")] for div in All_divs if div("a")!=None] for item in sublist]
            #i=i("p")+i("h5")+i("h4")+i("h3")+i("h2")+i("h1")
            text=[i.get_text(separator=u' ').replace(".",". ").replace("\n ",". ") for i in All_divs if i.get_text()!=None]

        except:
            print(f"error with: {FilePath}", end=". ")
            
            try:
                text=text.split("\n\n")
 
                print("--> text from reading as a text file.")
            except:
                print("also no text file")
                
        #leave out words longer than 100 characters to avoid undetected embedded images and other shit.
        text=[" ".join([y.replace("\n"," ").strip() for y in i.split(" ") if len(y)<100]) for i in text] 
       # text=["".join([y for y in i if len(y)<100]) for i in text]
    
    return pd.Series([Title,h1,h2,h3,text,linkName,linkUrl])
        
#df.file[2:6].apply(FileInfo)
print("This takes about 4 minutes")
print_time()        
df[["HTML_Title","h1","h2","h3","HTML_text","linkName","linkUrl"]]=df.filepath.apply(FileInfo)
print_time()

This takes about 4 minutes
Current Time = 10:57:11
error removing images: C:\Users\mr\Zotero\storage\MDTRC7HH\AI In Education.html
Current Time = 11:02:54


In [ ]:
df["filepath"][DoubleIndex]#.apply(FileInfo)

In [15]:
# Unify & drop columns.

df.loc[df["HTML_text"].apply(lambda x: x is not None), "HTML"]=True
df["HTML"]=df["HTML"].fillna(False)

df.loc[df["HTML"], "text"]=df.HTML_text
df.loc[df["HTML"], "title"]=df.HTML_Title
df.loc[df["HTML"], "links"]=df.linkUrl

df.language=df.language.replace(["en-US","en-GB","en-us","en_US","en_US","English"],"en")
df.language=df.language.replace(["nl","nl-NL","nederlands","nl-nl"],"nl")
df.language=df.language.replace("",None)

#improve text...
df.text=df.text.fillna("").apply(lambda l: [s.replace("..",". ").replace(". . ","") for s in l if isinstance(s,str)])

df.drop(columns=["HTML_text","HTML_Title","linkUrl","parentItem","h1","h2","h3"],inplace=True)


In [16]:
pd.set_option('display.max_colwidth', None)

DoubleIndex=df[df.text.duplicated()].index
#df=df.drop_duplicates(subset="text")
df.filepath[DoubleIndex]

IP5EHGEZ    C:\Users\mr\Zotero\storage\IP5EHGEZ\review-of-knowledge-sharing-education-365.html
Name: filepath, dtype: object

In [17]:
df.to_json("2023-07-30_Uni_Files_NLP.json")

In [ ]:
df=pd.read_json("2023-07-30_Uni_Files_NLP.json")



In [18]:
def Insert_title(text,Title):
    if Title!=None and type(text)==list:
        text=[Title.strip()]+text
        return text
    else:
        return text


df["text"]=df[["text","title"]].apply(lambda x: Insert_title(*x),axis=1)

In [19]:
def Splitter(paragraphs, max_len=5000):
    
    sentences=[]
    paragraphs_out=[]
    if isinstance(paragraphs,list):
        
        for paragraph in paragraphs:
            paragraph_out=[] 
       
            from nltk.tokenize import sent_tokenize           

            
            paragraph=paragraph.replace("\n",". ").replace("!"," ").replace("?"," ").replace("• ",". ").replace("..",". ").replace(". . ","")
            
            
            # fill in spaces after dot if followed by capital character
            import re
            regex = r"(?<=[a-zA-Z])\.(?=[A-Z][a-z])"
            subst = ". "
            paragraph = re.sub(regex, subst, paragraph, 0, re.MULTILINE)
            paragraph=paragraph.replace("  "," ").replace(" .",".").lstrip(". ")
            
            sentence=sent_tokenize(paragraph) # per paragraph
            sentence=[s for s in sentence if len(s)>1]

            counter = 0
            P="" # will be filled with sentences untill it has 5000 characters.
            for s in sentence:
                counter += len(s) # calculate the lenght if it would be added.

                if counter > max_len: # does not add the sentence to the paragraph if too long
                    
                    paragraph_out.append(P)
                    
                    L=len(paragraph_out[-1])
                    print(f"{L} + {len(s)} = {counter} --> split {len(paragraph_out)} times.")
                
                    counter=0
                    P=""
                    
                if counter < max_len:
                    P=P.strip()+" "+ s.strip()
            
            paragraph_out.append(P)

            sentences+=sentence
            
            paragraphs_out.extend(paragraph_out)
                
                
    sentences_len=[len(i) for i in sentences]
    paragraphs_len=[len(i) for i in paragraphs_out]
 
        
    return pd.Series([paragraphs_out,sentences,paragraphs_len,sentences_len])


df[["paragraphs","sentences","paragraphs_len","sentences_len"]]=df["text"].apply(Splitter, max_len=4500)
df["paragraph_sum"]=df.paragraphs_len.apply(lambda x: sum(x))

#df["text"].apply(Splitter)

4037 + 580 = 4598 --> split 1 times.
5013 + 321 = 4725 --> split 2 times.
4521 + 49 = 4533 --> split 1 times.
4125 + 580 = 4684 --> split 1 times.
5013 + 321 = 4725 --> split 2 times.
4823 + 38 = 4509 --> split 3 times.
4554 + 125 = 4602 --> split 4 times.
4478 + 115 = 4553 --> split 1 times.
4456 + 111 = 4526 --> split 1 times.
4537 + 46 = 4539 --> split 1 times.
4519 + 140 = 4632 --> split 1 times.
4442 + 102 = 4506 --> split 1 times.
4539 + 47 = 4546 --> split 1 times.
4478 + 244 = 4684 --> split 1 times.
4407 + 250 = 4626 --> split 1 times.
4387 + 189 = 4552 --> split 1 times.
4511 + 41 = 4502 --> split 1 times.
4363 + 258 = 4600 --> split 1 times.
4522 + 39 = 4515 --> split 1 times.
4536 + 55 = 4542 --> split 1 times.
4467 + 100 = 4527 --> split 1 times.
4403 + 339 = 4711 --> split 1 times.
4539 + 455 = 4611 --> split 2 times.
4505 + 142 = 4610 --> split 1 times.
4423 + 189 = 4576 --> split 1 times.
4491 + 125 = 4570 --> split 1 times.
4511 + 121 = 4586 --> split 1 times.
4512 + 8

4373 + 179 = 4512 --> split 1 times.
4674 + 189 = 4643 --> split 2 times.
4482 + 138 = 4580 --> split 1 times.
4514 + 97 = 4570 --> split 1 times.
4424 + 167 = 4559 --> split 1 times.
4551 + 149 = 4510 --> split 2 times.
4454 + 149 = 4582 --> split 1 times.
4533 + 75 = 4560 --> split 1 times.
4450 + 110 = 4514 --> split 1 times.
4542 + 196 = 4692 --> split 1 times.
4709 + 50 = 4515 --> split 2 times.
4443 + 144 = 4554 --> split 1 times.
4443 + 144 = 4554 --> split 1 times.
4531 + 53 = 4548 --> split 1 times.
4344 + 214 = 4518 --> split 1 times.
4622 + 177 = 4538 --> split 2 times.
4662 + 137 = 4580 --> split 3 times.
4518 + 191 = 4661 --> split 1 times.
4488 + 302 = 4766 --> split 1 times.
4798 + 120 = 4572 --> split 2 times.
4384 + 315 = 4675 --> split 1 times.
4829 + 109 = 4577 --> split 2 times.
4300 + 302 = 4579 --> split 1 times.
4798 + 120 = 4572 --> split 2 times.
4490 + 88 = 4542 --> split 1 times.
4494 + 86 = 4531 --> split 1 times.
4451 + 150 = 4551 --> split 1 times.
4538 + 

In [20]:
# Check the lenght of paragraphs

df[df.paragraphs_len.apply(lambda x: any(i > 5000 for i in x))]

key  \
RAM5QEQA  RAM5QEQA   
C6PW5SJM  C6PW5SJM   
JCB8V5T7  JCB8V5T7   

                                                                                         url  \
RAM5QEQA                 https://neerlandistiek.nl/2023/01/taalkundig-redeneren-met-chatgpt/   
C6PW5SJM             https://www.uu.nl/en/organisation/in-depth/unboxing-the-black-box-of-ai   
JCB8V5T7  https://www.uu.nl/en/organisation/faculty-of-geosciences/research/research-posters   

                                       filename                 Uni  \
RAM5QEQA  taalkundig-redeneren-met-chatgpt.html    Radboud Nijmegen   
C6PW5SJM      unboxing-the-black-box-of-ai.html  Utrecht University   
JCB8V5T7                  research-posters.html  Utrecht University   

                                                                   title  \
RAM5QEQA                                Taalkundig redeneren met ChatGPT   
C6PW5SJM    Unboxing the black box of AI - In depth - Utrecht University   
JCB8V5T7  Research Posters - Faculty of Geosciences - Utrecht University   

                               date itemType language  \
RAM5QEQA  2023-01-14 10:00:00+00:00  webpage       nl   
C6PW5SJM        2023-06-02 00:00:00  webpage       en   
JCB8V5T7        2023-07-17 00:00:00  webpage       en   

                                                                           filepath  \
RAM5QEQA  C:\Users\mr\Zotero\storage\RAM5QEQA\taalkundig-redeneren-met-chatgpt.html   
C6PW5SJM      C:\Users\mr\Zotero\storage\C6PW5SJM\unboxing-the-black-box-of-ai.html   
JCB8V5T7                  C:\Users\mr\Zotero\storage\JCB8V5T7\research-posters.html   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     

In [21]:

# just checkin if the long paragraphs are necessary...
df=df[df.title!='Research Posters - Faculty of Geosciences - Utrecht University']

#df=df[df["paragraph_sum"]<100000]


pd.set_option('display.max_colwidth', 255)

df[df["paragraph_sum"]>100000].filepath

VRYGVYFT                   C:\Users\mr\Zotero\storage\VRYGVYFT\20230607-jaarverslag-2022-cooperatie-surf-u.a.-gewaarmerkt.pdf
KB9PEGPE                                                 C:\Users\mr\Zotero\storage\KB9PEGPE\dpia-zoom-25-february-2022_0.pdf
WX4G68MK                                C:\Users\mr\Zotero\storage\WX4G68MK\hosa-domainarchitecture-iam-v1.0-eng-gb-final.pdf
ALDWBD7G                                   C:\Users\mr\Zotero\storage\ALDWBD7G\promises-of-ai-in-education-june-2022-def2.pdf
8AWPG27Z                                          C:\Users\mr\Zotero\storage\8AWPG27Z\sf_trendrapport_nl_v4-gecomprimeerd.pdf
WE6Q67A7                                               C:\Users\mr\Zotero\storage\WE6Q67A7\sf_trendrapport_v10_compressed.pdf
KBLFTTUZ    C:\Users\mr\Zotero\storage\KBLFTTUZ\surf-rapport-herijking-van-de-visie-op-de-digitale-leeromgeving_webversie.pdf
Name: filepath, dtype: object

In [22]:
df.to_json("2023-07-30_Uni_Files_NLP_splitter.json")


In [ ]:
df=pd.read_json("2023-07-30_Uni_Files_NLP_splitter.json")

In [ ]:
df.columns

In [ ]:
# Remove TextShit to save filespace
df.drop(columns=['text','title','paragraphs','paragraphs_len','paragraph_sum',"sentences_len","linkName"],inplace=True)

# Explode --> by sentence or by paragraph?

In [ ]:
#df=df.explode("sentences").drop_duplicates(subset="sentences").reset_index(drop=True)

df.paragraphs.explode()

In [ ]:
df.language.value_counts()

### I will filter in the analysis file. Therefore this code is not needed anymore...

ChatGPT_Terms="ChatGPT, Chat-GPT, GPT3, GPT-3, GPT-x, GPT-4, GPT4,\
Transformer, OpenAI, AI, hallucination, Text generation, LLM, GPT, Chatbot, Models, generative, Intelligence, Model"

import MyLib.nlp as nlp

df["AI_paragraphs"]=df.paragraphs.dropna().apply(nlp.filter_paragraphs,by=ChatGPT_Terms).dropna()

df["AI_Paragraphs_len"]=df["AI_paragraphs"].apply(lambda x: [len(i) for i in x])
df[df.AI_Paragraphs_len.apply(lambda x: any(i > 4999 for i in x))]


In [25]:
column="sentences"

#df=df[df.file.apply(lambda x: x.endswith("html"))]

df=df.explode(column).reset_index(drop=True)
df=df[df[column].apply(lambda x: type(x)==str)]
df=df.drop_duplicates(column)
df["LEN"]=df[column].apply(lambda x: len(x.split(" ")))
print(len(df))

39781


In [ ]:
df.head(3)

In [ ]:
#df[df.sentences.apply(lambda x: len(x.replace('[^a-zA-Z]', ''))<10)]["sentences"]

In [26]:
#remove tables of content
df=df[df.sentences.apply(lambda x: x.count(".")<10)]

#remove non-sense sentences by: if sentence is shorter than 10 characters without numbers.
df=df[df.sentences.apply(lambda x: len(x.replace('[^a-zA-Z]', ''))>10)]

df=df[df.sentences.apply(len)>15]



In [27]:
pd.set_option('display.max_colwidth', None)
PDF=df[df.HTML==False]

# test what the pdf sentences with dots look like now.

PDF[PDF.sentences.apply(lambda x: x.count(".")>8)].sentences.head(5)

18392                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                aspecten ter beoordeling aan de examenc ommissie voorgelegd:.. - frequentie van de fraude: herhaalde fraude.. - en/of de fraude opzettelijk heeft plaatsgevonden.. - en/of er sprake is van een vorm van identiteitsfraude.. - en/of er sprake is van het vervalsen of fabriceren van.
24535    Het gaatover de imp

In [28]:
# Check: remove short strings that dont resemble sentences.

n=16 # ab 17
c=df[df.sentences.apply(len)<n]
print("LEN: ", len(c))      
[print(i) for i in df[df.sentences.apply(len)<n].sentences]

LEN:  0


[]

In [29]:
df[df.sentences.apply(len)>4500]

Empty DataFrame
Columns: [key, url, filename, Uni, title, date, itemType, language, filepath, text, links, linkName, HTML, paragraphs, sentences, paragraphs_len, sentences_len, paragraph_sum, LEN]
Index: []

In [ ]:
df.columns

# RUN THE NLP PIPELINE

In [30]:
# test

test=pd.DataFrame(df.tail(5).to_dict())

print(pd. __version__)

test=nlp.NLP_Pipeline(test, text_column=column, target_language="en",sentiment=False)
test["source_language"]

2.0.3
Current Time = 11:07:33
Lenght:  5
cleaning done.
Current Time = 11:07:33
next: language.
language detection done.
Current Time = 11:07:33
Next: Translating...
Thes. #1 H. A po. In t. She . Current Time = 11:07:35
pure english text done. Next: Token & Lemmatizing.
Current Time = 11:07:35
Token & Lemmatizing done. Next: Remove Stopwords.
Current Time = 11:07:48


53746    nl
53747    nl
53748    nl
53749    nl
53750    nl
Name: source_language, dtype: object

In [31]:
test

key  \
53746  VTWCZBP7   
53747  VTWCZBP7   
53748  VTWCZBP7   
53749  VTWCZBP7   
53750  VTWCZBP7   

                                                                                                                                url  \
53746  https://communities.surf.nl/vraagbaak-online-onderwijs/artikel/deze-linkedin-posts-over-digitale-onderwijsinnovatie-wil-je-1   
53747  https://communities.surf.nl/vraagbaak-online-onderwijs/artikel/deze-linkedin-posts-over-digitale-onderwijsinnovatie-wil-je-1   
53748  https://communities.surf.nl/vraagbaak-online-onderwijs/artikel/deze-linkedin-posts-over-digitale-onderwijsinnovatie-wil-je-1   
53749  https://communities.surf.nl/vraagbaak-online-onderwijs/artikel/deze-linkedin-posts-over-digitale-onderwijsinnovatie-wil-je-1   
53750  https://communities.surf.nl/vraagbaak-online-onderwijs/artikel/deze-linkedin-posts-over-digitale-onderwijsinnovatie-wil-je-1   

                                                                 filename  \
53746  deze-linkedin-posts-over-digitale-onderwijsinnovatie-wil-je-1.html   
53747  deze-linkedin-posts-over-digitale-onderwijsinnovatie-wil-je-1.html   
53748  deze-linkedin-posts-over-digitale-onderwijsinnovatie-wil-je-1.html   
53749  deze-linkedin-posts-over-digitale-onderwijsinnovatie-wil-je-1.html   
53750  deze-linkedin-posts-over-digitale-onderwijsinnovatie-wil-je-1.html   

        Uni  \
53746  surf   
53747  surf   
53748  surf   
53749  surf   
53750  surf   

                                                                                              title  \
53746  Deze Linkedin-posts over (digitale) onderwijsinnovatie wil je niet missen | SURF Communities   
53747  Deze Linkedin-posts over (digitale) onderwijsinnovatie wil je niet missen | SURF Communities   
53748  Deze Linkedin-posts over (digitale) onderwijsinnovatie wil je niet missen | SURF Communities   
53749  Deze Linkedin-posts over (digitale) onderwijsinnovatie wil je niet missen | SURF Communities   
53750  Deze Linkedin-posts over (digitale) onderwijsinnovatie wil je niet missen | SURF Communities   

            date itemType  \
53746 2023-05-02  webpage   
53747 2023-05-02  webpage   
53748 2023-05-02  webpage   
53749 2023-05-02  webpage   
53750 2023-05-02  webpage   

                                                                                                     filepath  \
53746  C:\Users\mr\Zotero\storage\VTWCZBP7\deze-linkedin-posts-over-digitale-onderwijsinnovatie-wil-je-1.html   
53747  C:\Users\mr\Zotero\storage\VTWCZBP7\deze-linkedin-posts-over-digitale-onderwijsinnovatie-wil-je-1.html   
53748  C:\Users\mr\Zotero\storage\VTWCZBP7\deze-linkedin-posts-over-digitale-onderwijsinnovatie-wil-je-1.html   
53749  C:\Users\mr\Zotero\storage\VTWCZBP7\deze-linkedin-posts-over-digitale-onderwijsinnovatie-wil-je-1.html   
53750  C:\Users\mr\Zotero\storage\VTWCZBP7\deze-linkedin-posts-over-digitale-onderwijsinnovatie-wil-je-1.html   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   

In [32]:
## takes approximately 80 minutes (last time)
df=nlp.NLP_Pipeline(df, text_column=column, target_language="en",sentiment=False)

Current Time = 11:09:18
Lenght:  35610
cleaning done.
Current Time = 11:09:24
next: language.
language detection done.
Current Time = 11:15:18
Next: Translating...


NOLA. The . It m. Teac. We t. The . At s. Teac. The . Ther. The . The . The . This. In d. What. In S. A no. The . And . Aren. AI c. AI i. So w. The . Ther. Also. Ther. What. We h. Is t. How . Co-c. In o. How . Whic. What. Do w. To w. We k. What. It u. Do y. Sign. Cont. Addr. We u. Do y. Nati. NOLA. Ling. Neer. “Tha. Seve. Appa. Alth. But . I pu. Part. But . Char. For . The . It's. What. I ca. What. The . It i. And . But . You'. And . Seve. Let'. That. It p. But . But . The . The . But . What. Acco. And . Okay. Anyw. A co. The . If o. Beca. Sorr. Foll. My c. The . The . In t. With. If y. Stud. It h. To s. It i. But . And . I've. For . I wi. Shar. The . Sinc. Lect. 24 M. Dece. Sinc. Chat. 24 M. What. Did . Hone. I wa. And . If y. I be. I gu. But . I've. It c. Try . You . It m. It i. You . We'v. I wa. Ther. Ther. “The. Benu. So I. I do. From. The . Ther. I've. Yes,. Ther. I do. Tryi. Coin. Comp. Undo. Beca. And . The . In s. Yes,. Your. I su. This. Do n. Let . I im. With. For . The . The 

Fear. Hals. Reme. If t. ’ Hu. Stud. Agai. Or, . Hals. So t. Of w. ’ In. Fabi. I di. Conc. Arti. Read. | Te. What. Open. What. Rese. By l. Soci. Thes. The . Thin. At t. More. ICT . In t. In a. They. The . The . Lect. prof. Open. Info. Lega. They. Swit. But . An e. Oppo. This. By i. They. By l. Empl. Info. Regi. Know. In d. But . The . Walk. 00 h. Wort. 30 h. Cogn. Tim . Chat. 25 h. Stud. Ster. Retr. 8 pm. What. Walk. 00 h. Chec. Plea. Symp. Keyn. Wort. Para. Chat. Para. Retr. Keyn. What. Inau. Regi. Chat. H. J. With. This. The . To d. But . Chat. Howe. GPT . For . I kn. An o. Howe. Supp. When. You . H. J. This. You . You . On C. What. With. Espe. Cogn. Chat. H. J. But . The . Shor. One . Chat. The . The . But . Unfo. And . Belo. What. The . A pi. It i. Howe. H. J. Chat. And . Be c. Chec. It's. Then. Howe. Ask . This. This. The . In s. Just. So w. Belo. Ever. Thin. Or m. Chat. But . Chat. You . It c. But . H. J. Usua. Stil. Anot. You . And . Anot. One . You . Exac. This. dysl. Chat. Then

Lisa. We h. She . The . ” Zo. “Fru. This. An o. The . “Bra. )”, . “Too. Rese. Drea. We c. Poor. So t. And . The . ” Al. Ther. Ther. Inte. The . The . Chat. Chat. Toni. PhD . Brid. This. Kore. “For. ” Le. New . “Cha. You . Howe. Cryp. Lee'. Trus. “At . But . Beca. ” On. “Onl. But . “Int. ” Le. “Thi. I th. The . 00 i. Afte. On W. At E. We i. For . Duri. The . This. This. Mini. No p. Post. The . They. As a. Do y. WHAT. SIGN. Betw. Betw. Curs. That. The . Mayb. User. They. User. What. Rose. User. I wa. Now . What. Rose. User. Rose. User. User. Wisd. The . And . > He. > Ho. What. > Ho. > Wh. Unle. > Do. Sudd. How . Thos. And . Han . Han . 08/0. A fe. Stev. My f. 06/0. Ther. I fe. In a. No l. 22/0. Grou. I se. The . 15/1. Curs. Next. The . Also. nl w. The . Mean. Mean. One . They. So l. The . But . If y. We l. We s. Will. We s. This. As t. Furt. To g. Chat. For . 5 ba. Two . The . This. Last. AI -. It h. Yes,. We h. 16/0. One . Now,. From. Caps. Caps. The . As a. phot. Minh. That. It's. Mirr

In 2. "A l. Ther. When. The . This. In a. Data. Anot. ‘We . The . It l. “If . Data. Digi. Alla. For . ‘The. 000 . ‘How. This. One . For . This. Some. We w. The . Toge. ‘We . The . Subs. Arti. This. “The. “It . The . ’ Th. The . ‘The. We s. Resp. When. At t. Than. Cros. The . Her . ‘We . They. The . If t. We t. Beum. ‘We . When. Howe. We a. Shou. Link. Anot. Thes. Beum. We a. When. So t. Pers. 'The. ‘It . Peop. ’ Be. ‘In . We u. For . It i. Alla. Unti. If y. Asso. Arti. 'In . Then. We w. Beca. xCur. Crea. By b. ‘We . Ther. This. In a. “The. ’ Fo. “We . This. The . Lect. Lect. It's. #lin. #dig. Dr. . Dr. . by l. http. Cha . http. Cha . http. http. http. http. Text. Bett. Spec. http. prof. http. Mode. http. ● Re. ● Ov. ● Me. ● Su. ask1. ●~ 1. ➔ Ce. ● Us. ● It. ● Im. ● Le. http. http. http. http. d/em. Some. Unde. ● Ha. … to. A tr. We v. We c. Curi. Curi. Time. http. or c. Facu. Scie. In t. nl a. The . Expe. nl s. ..... nl... Musi. Here. Whic. Lies. A gr. The . The . At t. But . De V. One 

...

of t. redu. That. auto. for . trai. AI S. As t. syst. impl. equa. data. and . By e. cons. larg. econ. mode. know. in a. A re. emer. netw. prom. clas. fewe. This. insp. redu. and . shif. to t. The . cert. deve. open. skil. More. of A. maki. have. to A. In a. the . adva. and . new . poss. hard. Grap. GNN . data. The . The . but . send. natu. Towa. With. repr. to t. deep. Sinc. many. effi. open. Fede. In a. heal. cruc. to h. This. netw. part. mode. have. data. Cent. is n. comp. exce. wrap. from. This. thro. lear. eith. data. and . to a. is r. The . trai. mode. to g. less. This. orga. of d. the . skil. #Pri. econ. #Aut. This. oppo. so f. make. data. heal. By f. rese. lead. risk. data. Zodr. and . Synt. prot. trai. for . gene. of t. Synt. Anot. seri. This. alre. tic . If t. can . an e. Thro. secu. made. This. to p. soci. open. Ethi. With. of A. AI a. Thes. topi. resp. Ther. but . rele. Euro. The . tati. to m. acco. reli. Comm. stre. With. come. tech. addr. Fram. basi. A st. ity,. ing . Demo

Incr. open. Capg. to b. This. from. The . By p. open. SMEs. Quan. More. Aria. Cons. Rela. Koen. Serv. →A f. →Vir. →New. →An . tech. is u. othe. XR c. Educ. Whet. to b. find. The . ke-v. This. inte. comp. In t. Web3. The . Larg. appe. inst. Inte. Soci. fend. Educ. ment. cons. Rese. expe. Stud. Lear. This. Huma. XR m. or t. New . Tech. Tech. logi. Beco. very. At M. They. whil. The . open. #Dig. #Con. With. an X. With. Rese. Soci. Gene. of a. By c. XR c. Poin. It c. Remo. reli. With. powe. Some. open. XR p. virt. to c. In t. One-. This. For . inte. Virt. Ten . coll. Meta. skil. Huma. #Rig. #Ope. Virt. date. Many. and . VRCh. User. Tech. dail. Stud. New . Thes. For . buil. Epic. crea. The . How . The . to s. Spec. acce. Ther. tech. The . Devi. equi. Meta. a fu. In J. desi. The . Auto. Huma. #Glo. Virt. A ki. read. This. As X. beco. User. Curr. Hapt. grea. Thes. New . Feel. shoe. Meta. feed. The . Buil. Unit. om g. One . Just. XR e. For . Thes. numb. Look. get . can . Data. Auto. priv. #Cyb

beca. And . the . The . Ever. In d. ask . The . for . spec. a co. The . new . And . peri. stud. This. coop. In t. to i. And . old . depa. educ. has . foun. The . last. supp. beco. hope. of I. “One. this. lead. pref. good. can . depe. the . Mari. REVI. 4MIC. Micr. have. They. to m. A st. acqu. also. Micr. rubr. It m. must. Whet. cont. a di. cert. some. The . seem. badg. As a. (for. The . badg. this. open. Ther. at h. The . stil. Micr. The . At t. comp. Cont. will. poss. Such. of e. REVI. 5HYB. EDUC. Blen. mix . 'ble. subs. of l. In b. phys. ulti. So i. Hybr. stud. a li. coll. As a. spec. make. admi. The . In t. The . the . is c. phys. Of c. the . It i. forc. Ther. norm. to p. But . that. last. and . made. The . ling. know. Bare. The . lear. used. unra. wort. Blen. desi. coor. So o. once. One . Hybr. itie. upco. time. othe. so a. ther. And . both. REVI. Not . crat. on o. In r. Soci. inde. educ. spac. Smar. Smar. poss. wher. Insi. and . of a. Smar. The . Use . thin. Our . with. lear. In t

This. pers. for . are . Thin. went. With. shou. Sett. arch. usin. impo. to m. It i. to c. Phas. The . The . Data. this. That. info. tric. The . info. litt. Howe. educ. almo. gene. Cons. for . The . REVI. REVI. TO C. OR R. For . are . aspe. draw. In t. two . them. of G. It p. wher. of n. a li. Inno. a po. The . usab. Peak. enth. Thes. know. Thro. high. Expe. peri. REVI. Slop. clea. With. Ther. Plat. more. A pe. grow. Swam. slow. In a. obso. This. show. reco. On t. will. THE . Purp. The . posi. are . This. a co. lear. Inst. Divi. Divi. Dist. Disc. Use . REVI. TO T. The . work. defi. Inst. curr. (The. have. Find. Form. What. with. For . unde. This. REVI. The . the . We h. and . Our . this. of t. wise. Afte. educ. the . 'har. educ. educ. As C. For . the . At t. onli. Most. The . suff. ICT . enor. cont. ICT . mana. Inte. Band. equi. but . The . to o. lead. Educ. mana. plen. The . belo. cont. The . But . step. Lear. beca. firs. Lect. A hu. REVI. ICT . orga. The . In t. expe. the . As c. many

In t. She . Current Time = 12:08:55
pure english text done. Next: Token & Lemmatizing.
Current Time = 12:08:57
Token & Lemmatizing done. Next: Remove Stopwords.
Current Time = 12:22:34


In [34]:
df.columns

Index(['key', 'url', 'filename', 'Uni', 'title', 'date', 'itemType',
       'filepath', 'text', 'links', 'linkName', 'HTML', 'paragraphs',
       'sentences', 'paragraphs_len', 'sentences_len', 'paragraph_sum', 'LEN',
       'text_clean', 'letters_count', 'word_count', 'source_language',
       'pure_text', 'Lemmata', 'NoStopwords'],
      dtype='object')

In [36]:
# Remove TextShit to save filespace
df.drop(columns=['text','title','publicationTitle','paragraphs','paragraphs_len','paragraph_sum', 'text_clean'],inplace=True)

KeyError: "['publicationTitle'] not found in axis"

In [35]:
df.to_json("2023-07-30_ChatGPT_Sentences_NLP-Out_small.json")

In [ ]:
df.columns

df2=df[['Uni','FileKey','url','date', 'Title','linkName', 'linkUrl', 'AI_paragraphs','text_clean', 'letters_count', 'word_count',
       'language', 'source_language', 'pure_text', 'Lemmata', 'NoStopwords']]

In [ ]:
df2.to_json("2023-06-06_Zotero_AI_nlp_en2.json")